In this practice exercise, we will analyze Chipotle order data.  The file "Chipotle.tsv" contains this information in a tab separated file.  First, read in the data.  You might find the delimiter input to the pandas read_csv method useful. Use the head method to check that everything has been read in correctly.  

In [42]:
import pandas as pd
import numpy as np

#Write your code here
df_chipotle = pd.read_csv("Data/chipotle_orders.tsv",\
                         delimiter = "\t")

df_chipotle.head(10)

order_id  quantity                              item_name  \
0         1         1           Chips and Fresh Tomato Salsa   
1         1         1                                   Izze   
2         1         1                       Nantucket Nectar   
3         1         1  Chips and Tomatillo-Green Chili Salsa   
4         2         2                           Chicken Bowl   
5         3         1                           Chicken Bowl   
6         3         1                          Side of Chips   
7         4         1                          Steak Burrito   
8         4         1                       Steak Soft Tacos   
9         5         1                          Steak Burrito   

                                  choice_description item_price  
0                                                NaN     $2.39   
1                                       [Clementine]     $3.39   
2                                            [Apple]     $3.39   
3                                                NaN     $2.39   
4  [Tomatillo-Red Chili Salsa (Hot), [Black Beans...    $16.98   
5  [Fresh Tomato Salsa (Mild), [Rice, Cheese, Sou...    $10.98   
6                                                NaN     $1.69   
7  [Tomatillo Red Chili Salsa, [Fajita Vegetables...    $11.75   
8  [Tomatillo Green Chili Salsa, [Pinto Beans, Ch...     $9.25   
9  [Fresh Tomato Salsa, [Rice, Black Beans, Pinto...     $9.25

Now take a look at the dtypes attribute to see how the columns are stored.

In [43]:
#Write your code here
df_chipotle.dtypes

order_id               int64
quantity               int64
item_name             object
choice_description    object
item_price            object
dtype: object

We will write code to answer the following questions:

1. What fraction of customers order burritos versus burrito bowls?
2. What is the breakdown of salsa choice?
3. What is the average amount of money spent on a Chipotle order?

For question 1, we will use the apply method to create a column that will read "Burrito" for items that are a burrito, "Bowl" for items that are a bowl and "Other" for every other item.

In [44]:
def Burrito_or_Bowl(row, extra_input):
    item = row["item_name"]
    quantity = row["quantity"]
    if "Bowl" in item and quantity==1:
        return "Single Bowl"
    elif "Bowl" in item and quantity>1:
        return "Mult Bowl"
    elif "Burrito" in item:
        return "Burrito"
    else:
        return extra_input



Create new column called "Bowl_Burrito" and compute fractions of bowl versus burrito orders. The value_counts() method could be useful here.

In [45]:
#Write you code here
df_chipotle["Bowl_Burrito"] = df_chipotle.\
                                apply(Burrito_or_Bowl,\
                    extra_input = "drink/snack",\
                                     axis = 1)
df_chipotle.Bowl_Burrito.value_counts()

drink/snack    2119
Single Bowl    1269
Burrito        1172
Mult Bowl        62
Name: Bowl_Burrito, dtype: int64

For question 2, we need to write another function to be used with apply to create a column for the salsas. Let's look at the structure of the choice_description column:

In [46]:
df_chipotle.loc[4,:]

order_id                                                              2
quantity                                                              2
item_name                                                  Chicken Bowl
choice_description    [Tomatillo-Red Chili Salsa (Hot), [Black Beans...
item_price                                                      $16.98 
Bowl_Burrito                                                  Mult Bowl
Name: 4, dtype: object

In [47]:
#Look at choice_description
df_chipotle.loc[4,"choice_description"]

'[Tomatillo-Red Chili Salsa (Hot), [Black Beans, Rice, Cheese, Sour Cream]]'

In [48]:
#Another one
df_chipotle.loc[7,"choice_description"]

'[Tomatillo Red Chili Salsa, [Fajita Vegetables, Black Beans, Pinto Beans, Cheese, Sour Cream, Guacamole, Lettuce]]'

Notice that this column is a string, which contains what looks like a list of lists with the salsa type as the first entry in the list.  Make sure you get rid of the "(Hot)" in the salsa description.  

First, let's only look at orders without an NaN in the choice_description column.

In [49]:
#Drop NaN using dropna() method

df_chipotle.dropna(inplace = True)
df_chipotle.head()

order_id  quantity         item_name  \
1         1         1              Izze   
2         1         1  Nantucket Nectar   
4         2         2      Chicken Bowl   
5         3         1      Chicken Bowl   
7         4         1     Steak Burrito   

                                  choice_description item_price Bowl_Burrito  
1                                       [Clementine]     $3.39   drink/snack  
2                                            [Apple]     $3.39   drink/snack  
4  [Tomatillo-Red Chili Salsa (Hot), [Black Beans...    $16.98     Mult Bowl  
5  [Fresh Tomato Salsa (Mild), [Rice, Cheese, Sou...    $10.98   Single Bowl  
7  [Tomatillo Red Chili Salsa, [Fajita Vegetables...    $11.75       Burrito

In [50]:
#Write function here
def Get_Salsa(description):
    
    if "Salsa" in description.split(",")[0]:
        parsed_des = description.strip("[]").\
                            replace("-", " ").\
                            replace(",", "").\
                            split(" ")
        salsa_name = []
        for word in parsed_des:
            
            if word!="Salsa":
                salsa_name.append(word)
            else:
                return " ".join(salsa_name)
        return parsed_des
    else:
        return "No Salsa"
    


In [60]:
#Add the new column
#df_chipotle["Salsa"] = df_chipotle.choice_description.\
                            #apply(Get_Salsa)
    
df_chipotle.head()

Fresh Tomato             1365
Roasted Chili Corn        633
No Salsa                  576
Tomatillo Red Chili       480
Tomatillo Green Chili     322
Name: choice_description, dtype: int64

In [52]:
#Use value counts to get the breakdown
df_chipotle.Salsa.value_counts()

Fresh Tomato             1365
Roasted Chili Corn        633
No Salsa                  576
Tomatillo Red Chili       480
Tomatillo Green Chili     322
Name: Salsa, dtype: int64

For question 3, use iterrows to calculate the average price per order. Note that the item price column is a string, so first use string methods plut the as.type() method to recast this column as a float.

In [53]:
#Write your code here
df_chipotle["item_price"] = df_chipotle.item_price\
                .str.replace("$", "").astype("float")
df_chipotle.head()   

order_id  quantity         item_name  \
1         1         1              Izze   
2         1         1  Nantucket Nectar   
4         2         2      Chicken Bowl   
5         3         1      Chicken Bowl   
7         4         1     Steak Burrito   

                                  choice_description  item_price Bowl_Burrito  \
1                                       [Clementine]        3.39  drink/snack   
2                                            [Apple]        3.39  drink/snack   
4  [Tomatillo-Red Chili Salsa (Hot), [Black Beans...       16.98    Mult Bowl   
5  [Fresh Tomato Salsa (Mild), [Rice, Cheese, Sou...       10.98  Single Bowl   
7  [Tomatillo Red Chili Salsa, [Fajita Vegetables...       11.75      Burrito   

                 Salsa  
1             No Salsa  
2             No Salsa  
4  Tomatillo Red Chili  
5         Fresh Tomato  
7  Tomatillo Red Chili

In [58]:
#Get the average proce of each order
dict_total = {}
for index, row in df_chipotle.iterrows():
    
    order_id = row["order_id"]
    price = row["item_price"]
    
    if order_id in dict_total:
        dict_total[order_id]+=price
    else:
        dict_total[order_id] =price

np.mean(list(dict_total.values()))

16.5969558101473